In [ ]:
#!/usr/bin/python
# -*- coding: utf-8 -*-

#########################################################################################################
 #    2018/02/17    Python 3    Versión 1.0.0. cronIP.py
 #
 #        Envía un email informando del tipo de dispositivo, la ip y el momento en el cual establece
 #        conexión. Cada minuto envía un email con información relativa a temperaturas y tiempo de conexión.
 #   
 #    2017/12/30    Python 3    Versión 0.3    cronIP.py
 #    2017/10/28    Python 3    Versión 0.2    ip_mail.py
 # 
 #    Autor:        Juan de Dios Yáñez Ávila
 #    Contacto:     juandediosyanez@onw4rds.com
 #    Empresa:      Onwards
 #    Dirección:    www.onw4rds.com                                                                                                      
 #                                                                                                       
 #    Este programa se ejecuta gracias a crontab justo en el momento que el dispositivo es conectado y
 #    durante cada minuto desde ese mismo momento.           
 #                                                                  
 #    Conecta con una cuenta de correo electrónico de Gmail para informar sobre la IP de conexión.                                                                                         
#########################################################################################################


import smtplib, socket, commands, os
import datetime
import ftplib
import time
from email.mime.text import MIMEText
from io import open

# Tenemos que dar un tiempo al sistema para que se establezca conexión a red y no de error.
# Ya que necesitamos conocer la IP de conexión y si no tenemos conexión a internet tampoco
# iniciará el programa.
time.sleep(30)

#############
# Obtención de datos
eConexion = datetime.datetime.now()       # fecha de establecimiento de conexión
dispositivo = socket.gethostbyname()      # nombre del dispositivo
ip = commands.getoutput('hostname -I')    # IP del dispositivo
tTranscurrido = 0                         # tiempo transcurrido de conexión

#########
# Conocer temperatura de la CPU y la GPU
def get_cpu_temp():
    tempFile = open( "/sys/class/thermal/thermal_zone0/temp" )
    cpu_temp = tempFile.read()
    tempFile.close()
    cpu_temp = str(float(cpu_temp)/1000) +"ºC"
    return cpu_temp
    #Mostrar temperatura en grados Fahrenheit
    #return float(1.8*cpu_temp)+32

def get_gpu_temp():
    gpu_temp = commands.getoutput( "/opt/vc/bin/vcgencmd measure_temp" ).replace( 'temp=', '' ).replace( 'C', '' )
    gpu_temp = str(float(gpu_temp)) + "ºC"
    return gpu_temp
    #Mostrar temperatura en grados Fahrenheit
    # return float(1.8* gpu_temp)+32

########
# Enviar email con la información de la IP y de que todo marcha como debe
def email_ip():
    global eConexion
    global dispositivo
    global ip
    global iConexion
    global tTranscurrido

    direccion_ip = str(dispositivo) + " | " + str(ip)
    cpu_temp = get_cpu_temp()
    gpu_temp = get_gpu_temp()
    
    #SCRIPT PARA CREAR EL MENSAJE
    mensaje = MIMEText("""
                       Dispositivo:  {0}
                       IP:    {1}
                       Conexión establecida a las:  {2}
                       Temperatura de la CPU: {3}
                       Temperatura de la GPU: {4}
                       
                       Tiempo de funcionamiento aproximado: {5} segundos""" .format(dispositivo, ip, eConexion, cpu_temp, gpu_temp, tTranscurrido))
    mensaje['From'] = "onw4rds@gmail.com"
    mensaje['To'] = "onw4rds@gmail.com"
    mensaje['Subject'] = direccion_ip

    #SCRIPT PARA EL ENVIO DEL CORREO ELECTRONICO
    mailServer = smtplib.SMTP('smtp.gmail.com', 587)
    mailServer.ehlo()
    mailServer.starttls()
    mailServer.ehlo()
    mailServer.login("onw4rds@gmail.com", "#GOovh47536485q??")
    mailServer.sendmail("onw4rds@gmail.com", "onw4rds@gmail.com", mensaje.as_string())
    ## def sendmail(from_addr, to_addrs, msg, mail_options=[], rcpt_options=[])
    mailServer.quit()

while True:
    email_ip()
    time.sleep(60)
    tTranscurrido = tTranscurrido + 60
    
    
    

"""    
    
    
########
# Descargamos conexiones
def descargar_conexiones():
    global dispositivo

    ftp_servidor = 'ftp.cluster003.hosting.ovh.net'
    ftp_usuario  = 'onwardsepo'
    ftp_clave    = '5huJKxNZQU2F'
    ftp_raiz     = '/Archivos/conexiones/' # Carpeta raíz del servidor donde vamos a trabajar

    ## Descargamos una copia de la base de datos en el FTP
    fichero_origen = str(dispositivo)+".txt"
    fichero_destino = str(dispositivo)+".txt"
    # Conectamos con el servidor
    try:
        s = ftplib.FTP(ftp_servidor, ftp_usuario, ftp_clave)
        # class FTP(host='', user='', passwd='', acct='', timeout=_GLOBAL_DEFAULT_TIMEOUT, source_address=None)
        try:
            # Vamos al directorio operativas en el FTP
            s.cwd(ftp_raiz)
            # Dentro del directorio descargamos por binario el archivo de las lecturas
            s.retrbinary('RETR ' + fichero_origen, open(fichero_destino, 'wb').write)
            s.quit()
        except:
            ## Creamos la base de datos en csv y la subimos al servidor
            pass
    except:
        ## Error de conexión
        pass

######
# Actualizar conexiones
def actualizar_conexiones():
    global eConexion
    global dispositivo
    global ip
    global tConexion

    aux = open( (str(dispositivo)+".txt"), "r")
    aux2= aux.readlines()
    aux.close()
    aux3 = list()
    for conexion_dato in aux2:
        conexion_dato_procesado = conexion_dato.split("|")
        if((str(eConexion) == conexion_dato_procesado[0]) and (str(dispositivo) == conexion_dato_procesado[1])):
            actualizacion = str(eConexion) +"|"+ str(dispositivo) +"|"+ str(ip) +"|"+ str(tConexion)
            aux3.append(actualizacion)
        aux3.append(conexion_dato)
    aux = open( (str(dispositivo)+".txt"), "w")
    aux.writelines(aux3)
    aux.close()

#####
# Subir conexiones
def subir_conexiones():
    global dispositivo

    ftp_servidor = 'ftp.cluster003.hosting.ovh.net'
    ftp_usuario  = 'onwardsepo'
    ftp_clave    = '5huJKxNZQU2F'
    ftp_raiz     = '/Archivos/conexiones/' # Carpeta raíz del servidor donde vamos a trabajar
    
    fichero_origen = str(dispositivo)+".txt"
    fichero_destino = str(dispositivo)+".txt" 
    
    try:
        s = ftplib.FTP(ftp_servidor, ftp_usuario, ftp_clave)
        ## class FTP(host='', user='', passwd='', acct='', timeout=_GLOBAL_DEFAULT_TIMEOUT, source_address=None)
        try:
            # ¿? Se abre el fichero de origen en binario, modo 'rb'
            f = open(fichero_origen, 'rb')
            # Especificamos el lugar donde se guardará el archivo que subimos desde el dispositivo
            s.cwd(ftp_raiz)
            # Guarda en el FTP el archivo leído en binario. Sin este comando no se guarda.
            s.storbinary('STOR ' + fichero_destino, f)
            ## def storbinary(cmd, fp, blocksize=8192, callback=None, rest=None)
            f.close()
            s.quit()
        except:
            pass
    except:
        pass

###############





email_ip()
aux = eConexion
while(True):
    pConexion = datetime.datetime.now()    # paso de conexión que establece una acción
    tConexion = pConexion.minute - aux.minute
    if(tConexion > 1):
        tConexion = tConexion + 1
        descargar_conexiones()
        actualizar_conexiones()
        subir_conexiones()
        aux = pConexion
"""

In [ ]:
import commands
 
def get_cpu_temp():
    tempFile = open( "/sys/class/thermal/thermal_zone0/temp" )
    cpu_temp = tempFile.read()
    tempFile.close()
    return float(cpu_temp)/1000
    #Mostrar temperatura en grados Fahrenheit
    #return float(1.8*cpu_temp)+32

def get_gpu_temp():
    gpu_temp = commands.getoutput( "/opt/vc/bin/vcgencmd measure_temp" ).replace( 'temp=', '' ).replace( 'C', '' )
    return  float(gpu_temp)
    #Mostrar temperatura en grados Fahrenheit
    # return float(1.8* gpu_temp)+32

def main():
    print("Temperatura CPU: ", round(get_cpu_temp()))
    print("Temperatura GPU: ", round(get_gpu_temp()))

if __name__ == '__main__':
    main()